## model.WhileActivity

This notebook provides an example of OpenCLSim's __model.WhileActivity__. The while activity executes **sub_processes** until a **condition_event** is fulfilled. The condition event can be formulated based on the expression language documented in the project. 

#### 0. Import libraries

In [1]:
import datetime, time
import simpy

import shapely.geometry
import pandas as pd

import openclsim.core as core
import openclsim.model as model
import openclsim.plot as plot

#### 1. Initialise simpy environment

In [2]:
# setup environment
simulation_start = 0
my_env = simpy.Environment(initial_time=simulation_start)

#### 2. Define object classes
In this example we won't use object classes

#### 3. Create objects
##### 3.1. Create site object(s)
No site objects are created

##### 3.2. Create vessel object(s)
No vessel objects are created

##### 3.3 Create activity/activities

In [3]:
# initialise registry
registry = {}

In this example the while activity executes list of sub processes while the given stop condition is not met.

In [4]:
# create a list of the sub processes
sub_processes = [
    model.BasicActivity(
        env=my_env,
        name="Basic activity",
        registry=registry,
        duration=30,
    )
]

# create a 'while activity' that is made up of the 'sub_processes'
while_activity = model.WhileActivity(
    env=my_env,
    name="While activity of basic activities",
    registry=registry,
    sub_processes=sub_processes,
    condition_event=[{"type": "activity", "name": "While activity of basic activities", "state": "done"}],
)

In this case the stop condition is formulated such that the while activity only terminates after the while activity itself is been completed. This is problematic as this essentially forms an infinite loop. To make sure that the simulation comes to a stop we specify the simulation duration (until=100, ensures the simpy simulation runs until 100 time units have passed). 

#### 4. Register processes and run simpy

In [5]:
# initate the simpy processes defined in the 'while activity' and run simpy
model.register_processes([while_activity])
my_env.run(until=100)

#### 5. Inspect results
##### 5.1 Inspect logs

In [6]:
display(plot.get_log_dataframe(while_activity, [while_activity, *sub_processes]))

Activity           Timestamp ActivityState  \
0  While activity of basic activities 1970-01-01 00:00:00         START   
1  While activity of basic activities 1970-01-01 00:00:00         START   
2  While activity of basic activities 1970-01-01 00:00:30          STOP   
3  While activity of basic activities 1970-01-01 00:00:30         START   
4  While activity of basic activities 1970-01-01 00:01:00          STOP   
5  While activity of basic activities 1970-01-01 00:01:00         START   
6  While activity of basic activities 1970-01-01 00:01:30          STOP   
7  While activity of basic activities 1970-01-01 00:01:30         START   

         type                                   ref  
0         NaN                                   NaN  
1  subprocess  0d9a02b9-0352-4419-b952-c3b7731d47e5  
2  subprocess  0d9a02b9-0352-4419-b952-c3b7731d47e5  
3  subprocess  0d9a02b9-0352-4419-b952-c3b7731d47e5  
4  subprocess  0d9a02b9-0352-4419-b952-c3b7731d47e5  
5  subprocess  0d9a02b9-0352-4419-b952-c3b7731d47e5  
6  subprocess  0d9a02b9-0352-4419-b952-c3b7731d47e5  
7  subprocess  0d9a02b9-0352-4419-b952-c3b7731d47e5

##### 5.2 Visualise gantt charts

In [7]:
plot.get_gantt_chart([while_activity, *sub_processes])

Observe that the basic activity has a duration of 30 time units. The simulation stops after 100 time units. So the Basic activities can be completed three times only. A fourth time is started but interupted by the simulation end. 

The logs show that indeed three Basic activities have been completed. The fourth Basic activity was started a t = 90, but but never completed because the simulation ended at t = 100.

Also the gantt charts shows this. You can find the edges of the basic activities by hovering with your mouse over the Basic activity bar. The gantt chart only shows bars for completed activities (so that have a START _and_ a STOP in the log). As a consequence the horizontal time axis of the gantt chart ends at t = 90.